In [20]:
import pandas as pd
import sqlite3
from langchain_core.prompts import PromptTemplate
from langchain_google_genai import GoogleGenerativeAI
from langchain_core.output_parsers import StrOutputParser, JsonOutputParser
import json
import os
from dotenv import load_dotenv
import re
from reportlab.platypus import SimpleDocTemplate, Paragraph, Spacer
from reportlab.lib.styles import getSampleStyleSheet
from reportlab.lib.pagesizes import letter
import textwrap
from PIL import Image, ImageDraw, ImageFont
import time
import traceback
from io import StringIO 

In [21]:
load_dotenv("../.env")

True

In [22]:
# https://physionet.org/content/eicu-crd-demo/2.0.1/
def read_sqlite(dbfile):
    with sqlite3.connect(dbfile) as dbcon:
        tables = list(pd.read_sql_query("SELECT name FROM sqlite_master WHERE type='table';", dbcon)['name'])
        out = {tbl : pd.read_sql_query(f"SELECT * from {tbl}", dbcon) for tbl in tables}

    return out

all_table = read_sqlite('/Users/anjaneyabajaj/Documents/Semester_3-2/BITS_F471_LLM/project/physionet.org/files/eicu-crd-demo/2.0.1/sqlite/eicu_v2_0_1.sqlite3')

In [23]:
all_table.keys()

dict_keys(['apacheapsvar', 'apachepatientresult', 'apachepredvar', 'careplancareprovider', 'careplaneol', 'careplangeneral', 'careplangoal', 'careplaninfectiousdisease', 'diagnosis', 'hospital', 'infusiondrug', 'intakeoutput', 'lab', 'medication', 'microlab', 'note', 'pasthistory', 'patient', 'physicalexam', 'treatment', 'vitalaperiodic', 'vitalperiodic', 'nurseassessment', 'nursecare', 'nursecharting', 'respiratorycare', 'respiratorycharting', 'admissiondrug', 'admissiondx', 'allergy', 'customlab'])

In [24]:
TABLE_DESCRIPTIONS = {
    "patient" : "Contains patient demographics and admission and discharge details for hospital and ICU stays.",
    "physicalexam" : "The physical exam section allows users to document results of a physical exam.",
    "treatment" : "The treatment table allows users to document, in a structured format, specific active treatments for the patient.",
    "patienthistory" : "Provides information related a patient’s relevant past medical history.",
    "diagnosis" : "Patient diagnosis recorded in the active diagnosis table. Sequence does indicate relative severity. diagnosisPriority is not required.",
    "lab" : "Laboratory tests that have have been mapped to a standard set of measurements. Unmapped measurements are recorded in the customLab table.",
    "customlab" : "Standardized labs are included in the ‘lab’ table. Laboratory measurements that are not configured within the standard interface (for example, unmapped tests) are included in the customLab table.",
    "microlab" : "Microbiology data."
}

In [25]:
FIELD_DESCRIPTIONS = {
    "patient" : {
        "patientunitstayid" : "a globally unique identifier (GUID) used as a foreign key link to the patient table",
        "patienthealthsystemstayid" : "surrogate key for the patient health system stay (hospital stay)",
        "gender" : "gender of the patient: Male, Female, Unknown, Other, NULL",
        "age" : "age of the patient in full years. If the patient is over 89 years old specify “> 89” e.g.: 79, 36, 52, “> 89”, etc.",
        "ethnicity" : "picklist ethnicity of the patient: Asian, Caucasian, African American, Native American, Hispanic, Other/Unknown, NULL",
        "hospitalid" : "surrogate key for the hospital associated with the patient unit stay",
        "wardid" : "surrogate key for the ward associated with the patient unit stay",
        "apacheadmissiondx" : "Full path string of admission diagnosis for patients unit stay e.g.: Pulmonary valve surgery, Chest pain, unknown origin, Restrictive lung disease (i.e., Sarcoidosis, pulmonary fibrosis), etc.",
        "admissionHeight" : "admission height of the patient in cm e.g.: 160.0000, 182.9000, 175.3000, etc.",
        "hospitaladmittime24" : "time in 24 hour format of the hospital admit e.g.: “12:45”, “15:30”, “3:45”",
        "hospitaladmitoffset" : "number of minutes from unit admit time that the patient was admitted to the hospital",
        "hospitaladmitsource" : "location from where the patient was admitted to the hospital e.g.: Direct Admit, Floor, Chest Pain Center. etc.",
        "hospitaldischargeyear" : "year of the hospital discharge date",
        "hospitaldischargetime24" : "time in 24 hour format of when the hospital discharge event occurred e.g.: “12:45”, “15:30”, “3:45”",
        "hospitaldischargeoffset" : "number of minutes from unit admit time that the patient was discharged from the hospital",
        "hospitaldischargelocation" : "Structured list of location where the patient was discharged to from the hospital e.g.: Home, Nursing Home, Death, etc.",
        "hospitaldischargestatus" : "specifies patient’s condition upon leaving the hospital: Alive, Expired, or NULL",
        "unittype" : "the picklist unit type of the unit e.g.: MICU,Cardiovascular ICU,SDU/Step down,VICU,Neuro ICU,CCU,Virtual ICU,SICU,ICU,CCU-CTICU,Mobile ICU,CTICU,CSICU,Test ICU,Vent ICU,Burn-Trauma ICU",
        "unitadmittime24" : "time in 24 hour format of when the unit admit event occurred e.g.: “12:45”, “15:30”, “3:45”",
        "unitadmitsource" : "picklist location from where the patient was admitted e.g.: Emergency Room, Recovery Room, Direct Admit, etc.",
        "unitvisitnumber" : "identifies the visit number of the patient, i.e. if the patient’s hospital stay has multiple unit stays",
        "unitstaytype" : "patient’s unit stay type: stepdown/other, readmit for undo, admit, pre-admit, transfer, readmit",
        "admissionweight" : "admission weight of the patient in kilograms e.g.: 69.7000, 70.9000, 173.0000, etc.",
        "dischargeweight" : "patient weight at time of unit discharge in kilograms e.g.: 69.7000, 70.9000, 173.0000, etc.",
        "unitdischargetime24" : "time in 24 hour format of when the unit discharge event occurred e.g.: “12:45”, “15:30”, “3:45”",
        "unitdischargeoffset" : "number of minutes from unit admit time that the patient was discharged from the unit",
        "unitdischargelocation" : "Structured list of locations where the patient was discharged to from the unit e.g.: Other ICU (CABG), Other Hospital, Telemetry, Other Internal, Other ICU, Floor, Step-Down Unit (SDU), etc.",
        "unitdischargestatus" : "specifies patient’s condition upon leaving the unit: Alive, Expired, or NULL",
        "uniquepid" : "ID for a unique patient."
    }, 
    "physicalexam": {
        "physicalexamid" : "surrogate key for the physical exam item",
        "patientunitstayid" : "foreign key link to the patient table",
        "physicalexamoffset": "number of minutes from unit admit time that the physical exam item was entered",
        "physicalexampath": "the root path of the physical exam item e.g.: notes/Progress Notes/Physical Exam/Physical Exam/Constitutional/Vital Sign and Physiological Data/Resp Rate/Resp Current, notes/Progress Notes/Physical Exam/Physical Exam/Neurologic/GCS/Verbal Score/5, etc.",
        "physicalexamvalue": "Structured picklist of available of physical exam items: O2 Sat% Highest, withdraws to pain, HR Current, etc",
        "physicalexamtest": "The string builder value of the physical exam item e.g.: manual entry, 85, no wheezing, etc.",
    },
    "treatment" : {
        "patientunitstayid" : "foreign key link to the patient table",
        "treatmentid" : "surrogate key for the treatment",
        "treatmentoffset" : "number of minutes from unit admit time that the treatment was entered",
        "treatmentstring" : "the path of the treatment e.g.: neurologic",
        "activeupondischarge" : "denotes whether the treatment was active upon discharge from the unit: True or False"
    },
    "pasthistory" : {
        "pasthistoryid" : "surrogate key for the past history item",
        "patientunitstayid" : "foreign key link to the patient table",
        "pasthistoryoffset" : "number of minutes from unit admit time for the past history item",
        "pasthistoryenteredoffset" : "number of minutes from unit admit time that the past history item was entered",
        "pasthistorynotetype" : "note type for the past history item e.g.: Admission, Initial Consultation/Other, Re-Admission, etc.",
        "pasthistorypath" : "the root path of the past history item e.g.: notes/Progress Notes/Past History/Organ Systems/Hematology/Oncology (A)/Cancer Therapy/Chemotherapy/Cis-platinum, etc.",
        "pasthistoryvalue" : "Structured picklist of available past history items e.g.: Performed, hypercoagulable condition, COPD - no limitations, etc.",
        "pasthistoryvaluetext" : "the picklist value of the past history item e.g.: COPD - Moderate, CHF, Medication dependent, etc."
    },
    "diagnosis" : {
        "patientunitstayid" : "foreign key link to the patient table",
        "activeupondischarge" : "denotes whether the diagnosis was active upon discharge from the unit: True or False",
        "diagnosisid" : "surrogate key for the diagnosis",
        "diagnosisoffset" : "number of minutes from unit admit time that the diagnosis was entered",
        "diagnosisstring" : "the full pathstring of the diagnosis selected in eCareManager, the sections of the diagnosis will be separated by a",
        "icd9code" : "ICD-9 code for the diagnosis e.g.: 518.81, 537.9, 491.20, etc.",
        "diagnosispriority" : "picklist value which denotes whether the diagnosis was marked as: Primary, Major, or Other"
    },
    "lab" : {
        "patientunitstayid" : "foreign key link to the patient table",
        "labid" : "surrogate ID for the labs data",
        "labresultoffset" : "number of minutes from unit admit time that the lab value was drawn",
        "labtypeid" : "the type of lab that is represented in the values, 1 for chemistry, 2 for drug level, 3 for hemo, 4 for misc, 5 for non-mapped, 6 for sensitive, 7 for ABG lab",
        "labname" : "the picklist name of the lab e.g.: CPK, troponin - I, RBC, HCO3, Total CO2, etc. This is hospital specific.",
        "labresult" : "the numeric value of the lab e.g.: 7.3230,, 58.0000, 24.8000",
        "labresulttext" : "the text of the lab value e.g.: 7.257, 58.0 24.8",
        "labmeasurenamesystem" : "the measurement name of the lab e.g.: mm Hg, mmol/L, mEq/L, etc.",
        "labmeasurenameinterface" : "the measurement name of the lab from interfaces e.g.: mm Hg, mmol/L, mEq/L, etc.",
        "labresultrevisedoffset" : "number of minutes from unit admit time that the revised lab value was entered"
    },
    "customlab" : {
        "customlabid" : "surrogate ID for custom lab data", 
        "patientunitstayid" : "foreign key link to the patient table",
        "labotheroffset" : "number of minutes from unit admit time that the lab value was drawn",
        "labothertypeid" : "the type of custom lab that is represented in the values, 1 for chemistry, 2 for drug level, 3 for hemo, 4 for misc, 5 for non-mapped, 6 for sensitive, 7 for ABG lab",
        "labothername" : "the picklist name of the lab e.g.: CPK, troponin - I, RBC, HCO3, Total CO2, etc. This is hospital specific.",
        "labotherresult" : "the numeric value of the lab e.g.: 7.3230,, 58.0000, 24.8000",
        "labothervaluetext" : "the text of the lab value e.g.: 7.257, 58.0 24.8"
    },
    "microlab" : {
        "patientunitstayid" : "foreign key link to the patient table",
        "microlabid" : "surrogate key for the micro lab",
        "culturetakeoffset" : "number of minutes from unit admit time that the culture was taken",
        "culturesite" : "picklist site name from where the culture was taken e.g.: Wound, Drainage Fluid, Sputum, Expectorated, Nasopharynx, etc.",
        "organism" : "picklist organism found e.g.: Staphylococcus aureus, Pseudomonas aeruginosa, no growth, etc.",
        "antibiotic" : "picklist antibiotic used e.g.: ceftazidime, aztreonam, other, etc.",
        "sensitivitylevel" : "picklist sensitivity level of antibiotic: Intermediate, Resistant, or Sensitive"
    }
}


In [26]:
def extract_patient(all_tables, puid):
    patient_data = {}
    for tbl, df in all_tables.items():
        if "patientunitstayid" in df.columns and tbl in TABLE_DESCRIPTIONS:
            sub = df[df.patientunitstayid == puid]
            if not sub.empty:
                table_descr = TABLE_DESCRIPTIONS[tbl]
                field_descrs = FIELD_DESCRIPTIONS.get(tbl, {})
                rows = []
                for _, row in sub.iterrows():
                    row_dict = {
                        col: {"desc": field_descrs.get(col, ""), "value": row[col]}
                        for col in sub.columns
                    }
                    rows.append(row_dict)
                patient_data[tbl] = {
                    "table_description": table_descr,
                    "rows": rows
                }
    return patient_data

# patient_json = extract_patient(all_table, puid=141765)
# patient_json

In [27]:
prompt = PromptTemplate(
    input_variables=["patient_data"],
    template="""
You are a medical report generator being used to generate an elaborate 3 part report about a patient's medical history. This is NOT a summary, but IS a long form report - be as explicit as possible. For the following patient ICU stay data (JSON with tables and field descriptions), produce:

1) A structured PDF report with sections: Patient Info, History, Diagnoses, Treatments, Vital Trends, Lab Trends, Microbiology Tests, Physical Examination Results. If you feel information is insufficient for any of these subsections, simply return NULL.

2) A description of one or more visualization(s) (PNG) that would best reveal important patterns in the data.  
   - For each visualization, specify which variables go on which axes, any grouping or color-coding, and why this view is informative.  

3) One or more summary table(s) in CSV format that capture the most critical numerical or time-series trends you referenced above.  
   - Include appropriate column headers and units. Esnure that the CSV is properly formatted and can returned so that it can be read into a pandas daatframe.  

Return your output as a JSON with keys `"pdf_text"`, `"chart_description"`, and `"csv_data"`.

Minimum word count of each : 500 words

Patient data:
{patient_data}
"""
)

In [28]:
def make_pdf_paragraph(text, path):
    doc = SimpleDocTemplate(path, pagesize=letter,
                            leftMargin=30, rightMargin=30, topMargin=30, bottomMargin=30)
    styles = getSampleStyleSheet()
    story = []
    # split into paragraphs
    for para in text.split("\n\n"):
        story.append(Paragraph(para, styles['BodyText']))  
        story.append(Spacer(1, 12))
    doc.build(story)


In [29]:
def make_chart(desc, path,
               img_size=(600,400),
               margin=20,
               font_size=14,
               dpi=(300,300)):
    """
    Draws desc onto a white image, wraps lines automatically,
    and saves with the specified DPI.
    """
    img = Image.new("RGB", img_size, "white")                                  
    draw = ImageDraw.Draw(img)

    try:
        font = ImageFont.truetype("arial.ttf", font_size)
    except OSError:
        font = ImageFont.load_default()                                        

    wrapper = textwrap.TextWrapper(width=250)                                   
    lines = wrapper.wrap(desc)

    y = margin
    draw.multiline_text((margin, y), "\n".join(lines), fill="black", font=font, spacing=4)  

    img.save(path, dpi=dpi)                                                    


In [30]:
def csv_reader(output, filename):
    data = output.get("csv_data")
    if isinstance(data, list):
        df = pd.DataFrame(data)
    elif isinstance(data, str):
        df = pd.read_csv(StringIO(data))
    else:
        raise ValueError("Unsupported format for csv_data")
    df.to_csv(filename, index=False)

In [31]:
gemini = GoogleGenerativeAI(model="gemini-1.5-flash", api_key=os.getenv("GEMINI_API_KEY"))  
pipeline = prompt | gemini | JsonOutputParser()  

In [32]:
def generate_patient_files(row, output_dir):
       try:
              puid = row['patientunitstayid']

              pdata = extract_patient(all_table, puid)
              print("Extracted data")

              llm_json = pipeline.invoke({"patient_data": pdata})   
              print("LLM call output received")

              try:
                     spec = json.loads(llm_json)
              except:
                     spec = llm_json

              os.makedirs(output_dir, exist_ok=True)
              print("Loaded into json")

              make_pdf_paragraph(spec["pdf_text"], f"{output_dir}/{puid}_report.pdf")
              print("PDF generated")
              make_chart(spec["chart_description"], f"{output_dir}/{puid}_img.png",
                            img_size=(1200,800),
                            margin=40,
                            font_size=18,
                            dpi=(300,300))
              print("PNG generated")
              csv_reader(spec, f"{output_dir}/{puid}_data.csv")
              print("CSV generated")
              print()
       except Exception as e:
              print(f"Failed due to {e}!")
              traceback.print_exc()
       time.sleep(1)


In [33]:
for hsys_id, group in all_table["patient"].groupby("patienthealthsystemstayid"):
    patient_dir = f"testcases_2/patient_{hsys_id}"

    print(f"Processing patient {hsys_id}")
    for _, stay_row in group.iterrows():               
        generate_patient_files(stay_row, patient_dir)


Processing patient 129391
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 131022
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 131736
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 132209
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 133684
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 134042
Extracted data
LLM call output received
Loaded into json
PDF generated
Failed due to 'chart_description'!


Traceback (most recent call last):
  File "/var/folders/sp/k1nmj7js7kn3bs6939gy7f800000gq/T/ipykernel_50265/3682580007.py", line 21, in generate_patient_files
    make_chart(spec["chart_description"], f"{output_dir}/{puid}_img.png",
KeyError: 'chart_description'


Processing patient 134686
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 135332
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 135537
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 136669
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 137216
Extracted data
Failed due to Invalid json output: ```json
{
  "pdf_text": "**Patient Medical Report**\n\n**1. Patient Information**\n\n* **Patient Unit Stay ID:** 151867\n* **Patient Health System Stay ID:** 137216\n* **Gender:** Male\n* **Age:** 44\n* **Ethnicity:** Ca

Traceback (most recent call last):
  File "/Users/anjaneyabajaj/Documents/Semester_3-2/BITS_F471_LLM/project/projenv/lib/python3.10/site-packages/langchain_core/output_parsers/json.py", line 86, in parse_result
    return parse_json_markdown(text)
  File "/Users/anjaneyabajaj/Documents/Semester_3-2/BITS_F471_LLM/project/projenv/lib/python3.10/site-packages/langchain_core/utils/json.py", line 150, in parse_json_markdown
    return _parse_json(json_str, parser=parser)
  File "/Users/anjaneyabajaj/Documents/Semester_3-2/BITS_F471_LLM/project/projenv/lib/python3.10/site-packages/langchain_core/utils/json.py", line 166, in _parse_json
    return parser(json_str)
  File "/Users/anjaneyabajaj/Documents/Semester_3-2/BITS_F471_LLM/project/projenv/lib/python3.10/site-packages/langchain_core/utils/json.py", line 123, in parse_partial_json
    return json.loads(s, strict=strict)
  File "/Users/anjaneyabajaj/anaconda3/envs/ML_env/lib/python3.10/json/__init__.py", line 359, in loads
    return cls(*

Processing patient 137239
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 138053
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 138861
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 140376
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 140641
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 141090
Extracted data
Failed due to Invalid json output: ```json
{
  "pdf_text": "**Medical Report for Patient 002-10547**\n\n**1. Patient Information**\n\n* **Patient Unit Stay ID:** 156906\n* **Unique Patient ID:** 002-10547\n* **Gender:** Female\n* **Age:** 52\n* **Ethnicity:** Caucasian\n* **Admission Diagnosis:** Emphysema/bronchitis\n* **Admis

...

Traceback (most recent call last):
  File "/var/folders/sp/k1nmj7js7kn3bs6939gy7f800000gq/T/ipykernel_50265/3682580007.py", line 21, in generate_patient_files
    make_chart(spec["chart_description"], f"{output_dir}/{puid}_img.png",
KeyError: 'chart_description'


Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 786216
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 786322
Extracted data
LLM call output received
Loaded into json
PDF generated
PNG generated
CSV generated

Processing patient 787633
Extracted data
Failed due to Invalid json output: ```json
{
  "pdf_text": "**Medical Report: Patient 009-10008**\n\n**1. Patient Information**\n\n* **Patient Unit Stay ID:** 1061585\n* **Patient Health System Stay ID:** 787633\n* **Gender:** Female\n* **Age:** 51\n* **Ethnicity:** Asian\n* **Hospital ID:** 197\n* **Ward ID:** 477\n* **Unit Type:** Cardiac ICU\n* **Unit Admit Time:** 2015-XX-XX 23:02:00\n* **Unit Admit Source:** Direct Admit\n* **Unit Discharge Time:** 2015-XX-XX 21:50:00\n* **Unit Discharge Location:** Floor\n* **Unit Discharge Status:** Alive\n* **Admission Height:** 109.7 cm\n* **Admission Weight

Traceback (most recent call last):
  File "/Users/anjaneyabajaj/Documents/Semester_3-2/BITS_F471_LLM/project/projenv/lib/python3.10/site-packages/langchain_core/output_parsers/json.py", line 86, in parse_result
    return parse_json_markdown(text)
  File "/Users/anjaneyabajaj/Documents/Semester_3-2/BITS_F471_LLM/project/projenv/lib/python3.10/site-packages/langchain_core/utils/json.py", line 150, in parse_json_markdown
    return _parse_json(json_str, parser=parser)
  File "/Users/anjaneyabajaj/Documents/Semester_3-2/BITS_F471_LLM/project/projenv/lib/python3.10/site-packages/langchain_core/utils/json.py", line 166, in _parse_json
    return parser(json_str)
  File "/Users/anjaneyabajaj/Documents/Semester_3-2/BITS_F471_LLM/project/projenv/lib/python3.10/site-packages/langchain_core/utils/json.py", line 123, in parse_partial_json
    return json.loads(s, strict=strict)
  File "/Users/anjaneyabajaj/anaconda3/envs/ML_env/lib/python3.10/json/__init__.py", line 359, in loads
    return cls(*

Processing patient 787908
Extracted data


KeyboardInterrupt: 

In [ ]:
# all_table['patient'].apply(generate_patient_files, axis=1)